# Chroma DB

In [1]:
import chromadb

chroma_client = chromadb.Client()

# collection은 일종의 rdb로 따지면 table과 같은 개념 

In [2]:
collection = chroma_client.create_collection(name="my_collection")  # collection 객체 생성 

In [3]:
# collection에 데이터 추가 
collection.add(
    documents=[
        'This is a document about pineapple',
        'This is a document about mango',
        'This is a document about strawberry'
    ],
    ids=['id1', 'id2', 'id3']   # 문장을 구분할 id를 지정
)

In [4]:
# query를 써서 질의를 해서 조회
results = collection.query(
    query_texts=['This is a query document about vietnam'], # 검색할 문장
    n_results=2  # 유사도를 가지고 있는 문장을 검색해서 반환할 결과의 개수 
)

In [5]:
results # embedding을 가지고 있지 않고 문자열을 자체로 가지고 있기 때문에 벡터값을 가지고 계산한 것은 아님. 따라서 몇개를 가져오든 순서를 기반으로 가지고 옴. 

{'ids': [['id1', 'id2']],
 'embeddings': None,
 'documents': [['This is a document about pineapple',
   'This is a document about mango']],
 'uris': None,
 'included': ['metadatas', 'documents', 'distances'],
 'data': None,
 'metadatas': [[None, None]],
 'distances': [[1.2225853204727173, 1.2783520221710205]]}

### SciQ dataset 활용 ChromaDB 검색

In [6]:
# 데이터셋 로드 
from datasets import load_dataset

dataset = load_dataset("sciq", split="train")   # 학습용 데이터셋 로드 
dataset = dataset.filter(lambda x: x["support"] != "") # support가 빈값이 아닌 것에 대해서만 필터링 (공백인것 빼기) 

dataset # 특성 : 질문, 틀린답3, 틀린답1, 틀린답2, 정답, 추가적인 설명

c:\Users\USER\anaconda3\envs\vectordb_env\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Dataset({
    features: ['question', 'distractor3', 'distractor1', 'distractor2', 'correct_answer', 'support'],
    num_rows: 10481
})

In [7]:
# chroma db 클라이언트 객체 및 콜렉션 생성 
import chromadb

client = chromadb.Client()
collection = client.create_collection(name="sciq_support")

In [8]:
# !pip install huggingface_hub[hf_xet]

In [9]:
# 임베딩 모델 로드
from sentence_transformers import SentenceTransformer

embedding_model = SentenceTransformer("all-MiniLM-L6-v2") # 영어 임베딩하는데 가장 가벼운(가장 경량화된) 모델

In [10]:
supports = dataset["support"][:100]
support_embeddings = embedding_model.encode(supports).tolist()  # supports를 임베딩으로 변환, 리스트로 변환

In [11]:
len(support_embeddings[0])  # 384차원으로 임베딩되었다는 것을 볼 수 있다.

384

In [12]:
collection.add(
    ids=[str(i)for i in range(0, 100)],
    embeddings=support_embeddings,
    metadatas=[{"type": "support", "text": text} for text in supports]  # 메타데이터 : 제공하고 있는 데이터에 대한 설명/ 데이터에 대해 인지하기 위한 데이터 (이게 대체 뭔말???) / 직접 documents에 넣는 것보다 metadatas에 넣는 것이 훨씬 더 유연한 처리, 관리가 가능하다
)

In [13]:
questions = dataset["question"][:3]


In [14]:

question_embeddings = embedding_model.encode(questions).tolist()

results = collection.query(
    query_embeddings=question_embeddings,
    n_results=1
)

In [15]:
results

{'ids': [['36'], ['1'], ['2']],
 'embeddings': None,
 'documents': [[None], [None], [None]],
 'uris': None,
 'included': ['metadatas', 'documents', 'distances'],
 'data': None,
 'metadatas': [[{'text': 'Agents of Decomposition The fungus-like protist saprobes are specialized to absorb nutrients from nonliving organic matter, such as dead organisms or their wastes. For instance, many types of oomycetes grow on dead animals or algae. Saprobic protists have the essential function of returning inorganic nutrients to the soil and water. This process allows for new plant growth, which in turn generates sustenance for other organisms along the food chain. Indeed, without saprobe species, such as protists, fungi, and bacteria, life would cease to exist as all organic carbon became “tied up” in dead organisms.',
    'type': 'support'}],
  [{'type': 'support',
    'text': 'Without Coriolis Effect the global winds would blow north to south or south to north. But Coriolis makes them blow northeast

In [16]:
for i, q in enumerate(questions):
    print("Questions:", q)  # 현재 자연어로 된 질문
    print("Support:", results['metadatas'][i][0]['text'])   # 그에 대한 추가적인 설명 (support) n_results=1로 했기 때문에 1개만 가져옴(0번째 인덱스) -> 딕셔너리 형태니까 text를 통해 출력하게 만듬 
    print()

Questions: What type of organism is commonly used in preparation of foods such as cheese and yogurt?
Support: Agents of Decomposition The fungus-like protist saprobes are specialized to absorb nutrients from nonliving organic matter, such as dead organisms or their wastes. For instance, many types of oomycetes grow on dead animals or algae. Saprobic protists have the essential function of returning inorganic nutrients to the soil and water. This process allows for new plant growth, which in turn generates sustenance for other organisms along the food chain. Indeed, without saprobe species, such as protists, fungi, and bacteria, life would cease to exist as all organic carbon became “tied up” in dead organisms.

Questions: What phenomenon makes global winds blow northeast to southwest or the reverse in the northern hemisphere and northwest to southeast or the reverse in the southern hemisphere?
Support: Without Coriolis Effect the global winds would blow north to south or south to north

### Chroma DB를 활용한 키워드 기반 검색

In [17]:
# 샘플 데이터를 만듬 
documents = [
    "인공지능은 인간의 작업을 자동화하는 기술이다.",
    "기계 학습은 패턴을 학습하여 예측하는 기술이다.",
    "벡터 데이터베이스는 유사도를 기반으로 데이터를 검색하는 DB이다.",
    "딥러닝은 인공신경망을 활용한 기계 학습의 한 분야이다.",
    "강화 학습은 보상을 통해 최적의 행동을 학습하는 방법이다.",
    "자연어 처리 기술은 인간의 언어를 이해하고 생성할 수 있게 한다.",
    "AI는 이미지 인식, 음성 인식 등 다양한 분야에 활용된다.",
    "데이터 전처리는 모델 학습을 위한 필수 단계이다.",
    "오토인코더는 입력 데이터를 압축하고 복원하는 신경망이다.",
    "클러스터링은 데이터를 유사한 그룹으로 묶는 비지도 학습이다."
]

In [18]:
import chromadb
from sentence_transformers import SentenceTransformer

# ChromaDB 클라이언트, 컬렉션 생성
client = chromadb.PersistentClient(path='./chroma_db')    # PersistentClient는 데이터를 디스크에 저장하는 클라이언트(해당 경로에 데이터베이스를 저장장) / client는 메모리상에 저장됨 (메모리상에 저장된 데이터는 프로그램이 종료되면 데이터셋도 사라짐)
collection = client.get_or_create_collection(name='ai_documents')  # 컬렉션 생성 (없으면 생성, 있으면 가져옴)

# 텍스트 임베딩 모델 로드
model = SentenceTransformer('all-MiniLM-L6-v2')  # 경량화된 모델

In [19]:
for i, doc in enumerate(documents):
    embedding = model.encode(doc).tolist()
    collection.add(
        ids=[str(i)],
        embeddings=[embedding],
        metadatas=[{"text": doc}]
    )

In [20]:
query_keyword = 'AI'
query_embedding = model.encode(query_keyword).tolist()

results = collection.query(query_embeddings=query_embedding, n_results=2) 

for result in results['metadatas'][0]:
    print("검색된 문서:", result['text'])

검색된 문서: AI는 이미지 인식, 음성 인식 등 다양한 분야에 활용된다.
검색된 문서: 인공지능은 인간의 작업을 자동화하는 기술이다.


### 영화 추천 시스템

In [21]:
import pandas as pd
df = pd.read_csv('./data/tmdb_5000_movies.csv')
df

budget                                             genres  \
0     237000000  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
1     300000000  [{"id": 12, "name": "Adventure"}, {"id": 14, "...   
2     245000000  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
3     250000000  [{"id": 28, "name": "Action"}, {"id": 80, "nam...   
4     260000000  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
...         ...                                                ...   
4798     220000  [{"id": 28, "name": "Action"}, {"id": 80, "nam...   
4799       9000  [{"id": 35, "name": "Comedy"}, {"id": 10749, "...   
4800          0  [{"id": 35, "name": "Comedy"}, {"id": 18, "nam...   
4801          0                                                 []   
4802          0                [{"id": 99, "name": "Documentary"}]   

                                               homepage      id  \
0                           http://www.avatarmovie.com/   19995   
1          http://disney.go.com/disneypictures/pirates/     285   
2           http://www.sonypictures.com/movies/spectre/  206647   
3                    http://www.thedarkknightrises.com/   49026   
4                  http://movies.disney.com/john-carter   49529   
...                                                 ...     ...   
4798                                                NaN    9367   
4799                                                NaN   72766   
4800  http://www.hallmarkchannel.com/signedsealeddel...  231617   
4801                        http://shanghaicalling.com/  126186   
4802                                                NaN   25975   

                                               keywords original_language  \
0     [{"id": 1463, "name": "culture clash"}, {"id":...                en   
1     [{"id": 270, "name": "ocean"}, {"id": 726, "na...                en   
2     [{"id": 470, "name": "spy"}, {"id": 818, "name...                en   
3     [{"id": 849, "name": "dc comics"}, {"id": 853,...                en   
4     [{"id": 818, "name": "based on novel"}, {"id":...                en   
...                                                 ...               ...   
4798  [{"id": 5616, "name": "united states\u2013mexi...                es   
4799                                                 []                en   
4800  [{"id": 248, "name": "date"}, {"id": 699, "nam...                en   
4801                                                 []                en   
4802  [{"id": 1523, "name": "obsession"}, {"id": 224...                en   

                                original_title  \
0                                       Avatar   
1     Pirates of the Caribbean: At World's End   
2                                      Spectre   
3                        The Dark Knight Rises   
4                                  John Carter   
...                                        ...   
4798                               El Mariachi   
4799                                 Newlyweds   
4800                 Signed, Sealed, Delivered   
4801                          Shanghai Calling   
4802                         My Date with Drew   

                                               overview  popularity  \
0     In the 22nd century, a paraplegic Marine is di...  150.437577   
1     Captain Barbossa, long believed to be dead, ha...  139.082615   
2     A cryptic message from Bond’s past sends him o...  107.376788   
3     Following the death of District Attorney Harve...  112.312950   
4     John Carter is a war-weary, former military ca...   43.926995   
...                                                 ...         ...   
4798  El Mariachi just wants to play his guitar and ...   14.269792   
4799  A newlywed couple's honeymoon is upended by th...    0.642552   
4800  "Signed, Sealed, Delivered" introduces a dedic...    1.444476   
4801  When ambitious New York attorney Sam is sent t...    0.857008   
4802  Ever since the second grade when he first saw ... 

In [22]:
# overview(줄거리) 임베딩 -> 저장
# 메타데이터 title 포함해서 저장
# 영화 제목을 입력 -> 유사한 영화 추천 
# title -> overview -> 임베딩 -> vector DB에 저장

In [23]:
df.columns

Index(['budget', 'genres', 'homepage', 'id', 'keywords', 'original_language',
       'original_title', 'overview', 'popularity', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'tagline', 'title', 'vote_average',
       'vote_count'],
      dtype='object')

In [24]:
import chromadb
from sentence_transformers import SentenceTransformer

client = chromadb.PersistentClient(path='./chroma_db')
collection = client.get_or_create_collection(name='movies')

model = SentenceTransformer('all-MiniLM-L6-v2')

In [25]:
movies = [
    {
        "id": str(index),
        "title": row["title"],
        "overview": row["overview"] if pd.notna(row["overview"]) else ""  # overview가 NaN인 경우 빈 문자열로 대체
    } for index, row in df.iterrows()
]

In [26]:
for movie in movies:
    if movie["overview"]:   # 빈 문자열은 False로 처리 -> 임베딩 하지 않음 -> 저장하지 않음
        overview_embedding = model.encode(movie["overview"]).tolist()   # 리스트 형태로 컬렉션에 저장하기 위해 변환
        # 컬렉션에 영화 데이터 추가
        collection.add(
            ids=[movie["id"]],
            embeddings=[overview_embedding],
            metadatas=[{"title": movie["title"], "text": movie["overview"]}]
        )

In [27]:
# 1. 제목 입력 -> 줄거리를 찾고 -> 줄거리로 유사도 검색
input_title = "Inception"
query_text = df.loc[df['title'] == input_title, 'overview'].iloc[0]  # 제목에 해당하는 줄거리 찾기

query_embedding = model.encode(query_text).tolist()  # 줄거리 임베딩

results = collection.query(query_embeddings=[query_embedding], n_results=5)  # 유사한 영화 5개 검색

for result in results['metadatas'][0]:
    print("제목:", result['title'])
    print("줄거리:", result['text'])
    print()

제목: Inception
줄거리: Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious.

제목: Identity Thief
줄거리: When a mild-mannered businessman learns his identity has been stolen, he hits the road in an attempt to foil the thief -- a trip that puts him in the path of a deceptively harmless-looking woman.

제목: The Master of Disguise
줄거리: A sweet-natured Italian waiter named Pistachio Disguisey at his father Fabbrizio's restaurant, who happens to be a member of a family with supernatural skills of disguise. But moments later the patriarch of the Disguisey family is kidnapped Fabbrizio's former arch-enemy, Devlin Bowman, a criminal mastermind in an attempt to steal the world's most precious treasures from around the world. And it's up to Pistachio to track down Bowman and save 

In [28]:
# 2. 원하는 줄거리 입력 -> 유사도 검색 

# 1. 제목 입력 -> 줄거리를 찾고 -> 줄거리로 유사도 검색
query_text = "korea"

query_embedding = model.encode(query_text).tolist()  # 줄거리 임베딩

results = collection.query(query_embeddings=[query_embedding], n_results=5)  # 유사한 영화 5개 검색

for result in results['metadatas'][0]:
    print("제목:", result['title'])
    print("줄거리:", result['text'])
    print()

제목: Silmido
줄거리: On 31 January 1968, 31 North Korean commandos infiltrated South Korea in a failed mission to assassinate President Park Chung-hee. In revenge, the South Korean military assembled a team of 31 criminals on the island of Silmido to kill Kim Il-sung for a suicide mission to redeem their honor, but was cancelled, leaving them frustrated. It is loosely based on a military uprising in the 1970s.

제목: Tae Guk Gi: The Brotherhood of War
줄거리: In 1950, in South Korea, shoe-shiner Jin-tae Lee and his 18-year-old old student brother, Jin-seok Lee, form a poor but happy family with their mother, Jin-tae's fiancé Young-shin Kim, and her young sisters. Jin-tae and his mother are tough workers, who sacrifice themselves to send Jin-seok to the university. When North Korea invades the South, the family escapes to a relative's house in the country, but along their journey, Jin-seok is forced to join the army to fight in the front, and Jin-tae enlists too to protect his young brother. The

### 논물 pdf 내용 검색

In [29]:
# !pip install PyPDF2

In [30]:
import chromadb
from sentence_transformers import SentenceTransformer

client = chromadb.PersistentClient(path='./chroma_db')
# client.delete_collection(name='papers')  # 기존의 papers 컬렉션 삭제 (중복 방지)
collection = client.get_or_create_collection(name="papers")

model = SentenceTransformer('all-MiniLM-L6-v2')

In [31]:
papers = [
    {'id': '1', 'title': '딥러닝', 'path': './data/deep_learning.pdf'},
    {'id': '2', 'title': 'NLP', 'path': './data/nlp_paper.pdf'},
]

In [32]:
import PyPDF2

def extract_text_from_pdf(path):
    with open(path, 'rb') as f:
        reader = PyPDF2.PdfReader(f)
        text = " ".join([page.extract_text() for page in reader.pages if page.extract_text()])

    return text

In [33]:
for paper in papers:
    text = extract_text_from_pdf(paper['path'])  # PDF에서 텍스트 추출
    embedding = model.encode(text).tolist()  # 텍스트 임베딩
    collection.add(
        ids=[paper['id']],
        embeddings=[embedding],
        metadatas=[{"title": paper['title']}],  # 메타데이터에 제목과 텍스트 저장
        documents=[text]  # 문서 내용 저장 (PDF에서 추출한 텍스트)
    )


In [34]:
collection.get()  # 컬렉션에 저장된 모든 데이터 조회 / 따로 명시적으로 작성성하지 않으면 inluded에 다른 것을 불러오지 않음음

{'ids': ['1', '2'],
 'embeddings': None,
 'documents': ['HAL Id: hal-04206682\nhttps://hal.science/hal-04206682v1\nSubmitted on 14 Sep 2023\nHAL is a multi-disciplinary open access\narchive for the deposit and dissemination of sci-\nentific research documents, whether they are pub-\nlished or not. The documents may come from\nteaching and research institutions in F rance or\nabroad, or from public or private research centers.L’archive ouverte pluridisciplinaire HAL , est\ndestinée au dépôt et à la diffusion de documents\nscientifiques de niveau recherche, publiés ou non,\némanant des établissements d’enseignement et de\nrecherche français ou étrangers, des laboratoires\npublics ou privés.\nDeep learning\nY ann Lecun, Y oshua Bengio, Geoffrey Hinton\nT o cite this version:\nY ann Lecun, Y oshua Bengio, Geoffrey Hinton. Deep learning. Nature, 2015, 521 (7553), pp.436-444.\n\uffff10.1038/nature14539\uffff. \uffffhal-04206682\uffff 1Facebook AI Research, 770 Broadway, New York, New York 10

In [35]:
# include 안에 넣게 되면 어떻게 가져오는지 확인
results = collection.get(
    include=["embeddings", 'documents' ,'metadatas']
    )  # include 매개변수 지정하지 않으면 metadats, documents 두가지만 가지고옴

# 검색은 .query() 메소드를 사용 / .get() 메소드는 저장되어있는 데이터를 전부.

for emb in results['embeddings']:
    print(len(emb))  # 임베딩 벡터의 길이 확인 (384차원)

384
384


In [36]:
query_text = 'Natural Language'
query_embedding = model.encode(query_text).tolist()  # 쿼리 텍스트 임베딩
results = collection.query(query_embeddings=[query_embedding], n_results=1)
results['metadatas'][0][0]['title']  # 검색된 논문 제목
results

{'ids': [['2']],
 'embeddings': None,
 'documents': [['“9781405155816_6_index” — 2010/5/8 — 12:21 — page 776 — #14 “9781405155816_1_000” — 2010/5/14 — 16:54 — page i — #1\nThe Handbook of Computational Linguisticsand Natural Language Processing “9781405155816_1_000” — 2010/5/14 — 16:54 — page ii — #2\nBlackwell Handbooks in Linguistics\nThis outstanding multi-volume series covers all the major subdisciplines within linguistics today and,when complete, will offer a comprehensive survey of linguistics as a whole.Already published:The Handbook of Child LanguageEdited by Paul Fletcher and Brian MacWhinneyThe Handbook of Phonological TheoryEdited by John A. GoldsmithThe Handbook of Contemporary Semantic TheoryEdited by Shalom LappinThe Handbook of SociolinguisticsEdited by Florian CoulmasThe Handbook of Phonetic Sciences, 2nd EditionEdited by William J. Hardcastle and John LaverThe Handbook of MorphologyEdited by Andrew Spencer and Arnold ZwickyThe Handbook of Japanese LinguisticsEdited by 

# FAISS DB
- Facebook AI Similarity Search

In [37]:
# !pip install faiss-cpu
# !pip install faiss-gpu

# 영화 추천 시스템

In [38]:
import faiss
import numpy as np
from sentence_transformers import SentenceTransformer

model = SentenceTransformer('all-MiniLM-L6-v2')


In [44]:
movies = [
    {'id': 0, "title": "인셉션", "description": "꿈속에서 다른 사람의 생각을 조작하는 스토리"},
    {'id': 1, "title": "인터스텔라", "description": "시간과 차원을 넘나드는 우주 탐사 이야기"},
    {'id': 2, "title": "기생충", "description": "두 가족의 계급 갈등을 그린 블랙코미디"},
    {'id': 3, "title": "어벤져스: 엔드게임", "description": "슈퍼히어로들이 우주를 구하기 위해 싸우는 이야기"},
    {'id': 4, "title": "타이타닉", "description": "비극적인 배 사고 속에서 피어난 사랑 이야기"},
    {'id': 5, "title": "라라랜드", "description": "꿈을 쫓는 두 예술가의 로맨스"},
    {'id': 6, "title": "매트릭스", "description": "가상현실과 인공지능의 세상에서 벌어지는 전투"},
    {'id': 7, "title": "쇼생크 탈출", "description": "희망을 잃지 않고 감옥에서 탈출한 한 남자의 이야기"},
    {'id': 8, "title": "해리 포터와 마법사의 돌", "description": "마법 세계에 입학한 소년의 첫 모험"},
    {'id': 9, "title": "반지의 제왕: 반지 원정대", "description": "절대 반지를 파괴하기 위한 여정의 시작"},
    {'id': 10, "title": "다크 나이트", "description": "고담시를 지키기 위한 배트맨과 조커의 대결"},
    {'id': 11, "title": "조커", "description": "한 남자가 광기에 빠져 조커로 변해가는 이야기"},
    {'id': 12, "title": "업", "description": "풍선으로 집을 날리는 노인의 감동적인 모험"},
    {'id': 13, "title": "코코", "description": "죽은 자들의 세계에서 가족의 의미를 깨닫는 이야기"},
    {'id': 14, "title": "겨울왕국", "description": "얼음의 마법을 가진 공주의 자아 찾기 여정"},
    {'id': 15, "title": "주라기 공원", "description": "공룡이 되살아난 테마파크에서 벌어지는 사건"},
    {'id': 16, "title": "킹스맨: 시크릿 에이전트", "description": "신사 스파이들의 스타일리시한 액션"},
    {'id': 17, "title": "미션 임파서블: 고스트 프로토콜", "description": "불가능한 미션을 수행하는 IMF 요원의 활약"},
    {'id': 18, "title": "월-E", "description": "지구 폐허 속 외로운 로봇의 사랑과 모험"},
    {'id': 19, "title": "드라이브", "description": "낮엔 스턴트맨, 밤엔 범죄자의 이중생활"}
]


In [ ]:
descriptions = [movie['description'] for movie in movies]   # 영화 설명 리스트 생성

desc_emb = np.array([model.encode(description) for description in descriptions], dtype='float32')

In [46]:
dim = desc_emb.shape[1] # 차원 수 (임베딩 벡터의 길이)
idx = faiss.IndexFlatL2(dim)  # L2 거리 기반의 인덱스 생성 (유클리드 거리)  /  chroma db에서 컬렉션을 만들고 데이터를 추가하는 것과 유사한 역할 / 컬렉션은 데이터를 저장하는 것, 인덱스는 검색을 위한 구조체)
idx.add(desc_emb)  # idx에 설명 임베딩 추가 (faiss.IndexFlatL2는 데이터 구조체라고 생각하면 됨) / 데이터를 추가하는 것과 유사한 역할을 함 (faiss는 검색을 위한 구조체, chroma db는 데이터를 저장하는 것)

In [ ]:
# 벡터db에서 검색한다 -> 임베딩된것과 유사한 것을 찾는다는 말. 
# 위에서 임베딩된 것 : descriptions
# idx : collection같은 것. 
# dim : 차원 수 (임베딩 벡터의 길이)

In [ ]:
query_text = "조커"
query_embed = np.array([model.encode(query_text)], dtype='float32')  # 쿼리 텍스트 임베딩 / datatype을 float32로 변환하기 위해 np.array로 감싸줌

In [61]:
top_n = 5  # 검색할 상위 n개
# faiss는 검색을 위한 구조체이기 때문에 검색을 위한 메소드가 존재
distances, indices = idx.search(query_embed, top_n)  # 쿼리 임베딩과 유사한 상위 5개 검색s
# 결과 : (거리, 인덱스) / 거리 : 쿼리와 가장 가까운 것부터 나옴 / 인덱스 : movies 리스트에서의 인덱스 번호

In [51]:
print(distances)
print(indices)

[[0.7128261  0.9000239  0.91464114 1.0056337  1.0385551 ]]
[[10 11  2 18 15]]


In [62]:
for i in range(top_n):
    movie_id = indices[0][i]  # 인덱스 번호로 영화 ID 찾기
    print(f'{i+1}번째 추천: {movies[movie_id]["title"]} (유사도 거리: {distances[0][i]:.2f})')  # 영화 제목과 거리 출력

1번째 추천: 다크 나이트 (유사도 거리: 0.71)
2번째 추천: 조커 (유사도 거리: 0.90)
3번째 추천: 기생충 (유사도 거리: 0.91)
4번째 추천: 월-E (유사도 거리: 1.01)
5번째 추천: 주라기 공원 (유사도 거리: 1.04)


### 사용자 맞춤 뉴스 추천 <실습>

In [ ]:
# 뉴스의 제목을 10, 20 크롤링
# 키워드 입력
# FAISS 활용해 맞춤 뉴스 추천